# <span style="color:blue">Delaware Valley Region School Atlas</span>

This atlas visualizes schools in the Delaware Valley region. The map plots schools based on their type, focusing on the following four categories:

- **District Public** (Blue)
- **Charter Public** (Green)
- **Secular Private** (Purple)
- **Religious Private** (Red)

The color-coded markers represent each school type, providing a clear geographical overview.


In [1]:
# Basic Imports
import os
import zipfile
import time

# Data Management Imports
import pandas as pd
import openpyxl

# Visualizations
import matplotlib.pyplot as plt
import geopandas as gpd
import folium
from geopy.geocoders import Nominatim

In [4]:
### CREATING THE GEODATAFRAME FOR BOUNDARIES OF DEL.VAL. REGION

# Making path to the folder where shapefiles are located
shapefile_folder = './shapefiles' 

# Find the shapefile (.shp) in the folder
shapefile_path = next((os.path.join(shapefile_folder, f) for f in os.listdir(shapefile_folder) if f.endswith('.shp')), None)

if shapefile_path:
    # Read the shapefile using GeoPandas
    gdf = gpd.read_file(shapefile_path)

    # Check the CRS (Coordinate Reference System) and reproject if necessary
    if gdf.crs != 'EPSG:4326':
        gdf = gdf.to_crs(epsg=4326)  # Reproject to EPSG:4326


    # Filter the GeoDataFrame for counties in the Delaware Valley region
    delaware_valley_counties = [
        "Philadelphia", "Bucks", "Chester", "Delaware", "Montgomery",  # Pennsylvania counties
        "Burlington", "Camden", "Gloucester", "Mercer",  # New Jersey counties
        "New Castle",  "Kent" # Delaware county
    ]
    
    delaware_valley_gdf = gdf[gdf['co_name'].isin(delaware_valley_counties)]
    delaware_valley_gdf = delaware_valley_gdf[delaware_valley_gdf.is_valid]

    print("Counties in the Delaware Valley Region after filtering for valid geometries:")
    print(delaware_valley_gdf['co_name'].unique())

    # Display the first few rows of the filtered GeoDataFrame
    # print("Counties in the Delaware Valley Region:")
    # print(delaware_valley_gdf.head())
else:
    print("Error: No shapefile (.shp) found in the folder.")


Counties in the Delaware Valley Region after filtering for valid geometries:
['Kent' 'New Castle' 'Montgomery' 'Camden' 'Gloucester' 'Mercer'
 'Burlington' 'Bucks' 'Chester' 'Delaware' 'Philadelphia']


In [5]:
### GEOCODING SCHOOLS FROM THE DATA & PLOTTING ON MAP

# Load the schools data
# Download the Schools Database Google Sheet to your local machine as a Microsoft Excel file.
# Here, be sure to change the file path below to the respective Schools Database Excel file on your local machine.
schools = pd.read_excel('/Users/jazminb./Desktop/RA_Fall2024/AtlasData/PhiladelphiaSchools.xlsx')

# Initialize geolocator
geolocator = Nominatim(user_agent="school_locator")

# Function to get latitude and longitude using the automated geolocator with manual entry option.
def get_coordinates(name, address):
    try:
        location = geolocator.geocode(address)
        if location:
            return location.latitude, location.longitude
        else:
            print(f"Could not geocode: {name} at {address}")
            # This is the manual entry option if the automated geolocator can not find the information.
            manual_entry = input(f"Enter coordinates for {name} (format: 'latitude,longitude') or leave blank to skip: ")
            if manual_entry:
                try:
                    lat, lon = map(float, manual_entry.split(','))
                    return lat, lon
                except ValueError:
                    print(f"Invalid format for {name}. Skipping.")
            return None, None
    except Exception as e:
        print(f"Error for {name} at {address}: {e}")
        return None, None

# Dataframe to store results
results = []

# Loop through schools DataFrame using .iterrows()
for _, school in schools.iterrows():
    name = school["name"]
    address = school["address"]
    lat, lon = get_coordinates(name, address)
    results.append({
        "name": name, 
        "type": school["type"], 
        "address": address, 
        "county": school["county"], 
        "latitude": lat, 
        "longitude": lon
    })
    time.sleep(1)  # Pause to respect API usage limits

# Convert results to a DataFrame
school_coords = pd.DataFrame(results)

# Define colors for each school type
type_colors = {
    "District Public": "blue",
    "Charter Public": "green",
    "Secular Private": "purple",
    "Religious Private": "red"
}

# Create a map centered on Philadelphia
m = folium.Map(location=[39.9526, -75.1652], zoom_start=12)
folium.GeoJson(delaware_valley_gdf).add_to(m)

# Plot each school on the map with the correct color based on its type
for _, row in school_coords.iterrows():
    if not pd.isna(row["latitude"]) and not pd.isna(row["longitude"]):
        # Set the color based on the type of school
        marker_color = type_colors.get(row["type"], "gray")  # Default to gray if type is not found
        
        # Add marker to the map with the correct color
        folium.Marker(
            location=[row["latitude"], row["longitude"]],
            popup=f"{row['name']} ({row['type']})<br>County: {row['county']}",
            tooltip=f"{row['name']} ({row['type']}) - {row['county']}",  # Shows name, type, and county in the tooltip
            icon=folium.Icon(color=marker_color)  # Apply the color
        ).add_to(m)

m

Could not geocode: Belmont CS at 1630 Locust Street, 3rd Floor, Philadelphia, PA, 19103-
Error for Christopher Columbus CS at South Building, 1242-46 S 13th St, Philadelphia, PA, 19147-4528: HTTPSConnectionPool(host='nominatim.openstreetmap.org', port=443): Max retries exceeded with url: /search?q=South+Building%2C+1242-46+S+13th+St%2C+Philadelphia%2C+PA%2C+19147-4528&format=json&limit=1 (Caused by ReadTimeoutError("HTTPSConnectionPool(host='nominatim.openstreetmap.org', port=443): Read timed out. (read timeout=1)"))
Could not geocode: Community Academy of Philadelphia CS at 1100 East Erie Ave, Philadelphia, PA, 19124-5424
Could not geocode: Eugenio Maria DE Hostos CS at 4322 N 5th Street, 3rd Flr, Philadelphia, PA, 19140-
Could not geocode: Folk Arts-Cultural Treasures CS at 1023 Callowhill St, Philadelphia, PA, 19123-3709
Could not geocode: Franklin Towne CHS at 5301 Tacony St Building 108, Bx 310, Philadelphia, PA, 19137-2308
Could not geocode: Imhotep Institute CHS at 6201 N. 21st 